In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import folium
from folium import plugins
import ipywidgets
from branca.element import Figure
import json
import geopandas as gpd
import us
import os

# Importing universities and covid19 data from earlier cleaning

In [2]:
#Importing universities and covid19 data
df = pd.read_csv("University_Covid19_Variables.csv")
pd.set_option('display.max_columns', None)
df.head()

Unnamed: 0                   Institution  Control State  \
0           0  Abilene Christian University  Private    TX   
1           1     Academy of Art University  Private    CA   
2           2            Adelphi University  Private    NY   
3           3                Adrian College  Private    MI   
4           4           Agnes Scott College  Private    GA   

                                            Category  \
0  <a href="https://www.acu.edu/coronavirus/april...   
1  <a href="https://youtu.be/xxsrSGINzEU" target=...   
2  <a href="https://news.adelphi.edu/au_news/adel...   
3  <a href="http://adrian.edu/news/ac-president-d...   
4  <a href="https://www.agnesscott.edu/coronaviru...   

                       Plan        Lat        Long  January_Death  \
0    Planning for in-person  32.469732  -99.708098            0.0   
1    Planning for in-person  37.787725 -122.400662            0.0   
2  Proposing a hybrid model  40.719887  -73.652254            0.0   
3    Planning for in-person  41.898705  -84.059241            0.0   
4    Planning for in-person  33.768506  -84.294535            0.0   

   February_Death  March_Death  April_Death  May_Death  June_Death  \
0             0.0        227.0      11438.0    39119.0      1678.0   
1             0.0        910.0      28692.0    97739.0      4251.0   
2             0.0       6208.0     330353.0   682785.0     23959.0   
3             0.0        920.0      59532.0   148883.0      5516.0   
4             0.0        622.0      17746.0    49289.0      2074.0   

   January_Hospitalized  February_Hospitalized  March_Hospitalized  \
0                   0.0                    0.0                 0.0   
1                   0.0                    0.0                 0.0   
2                   0.0                    0.0             86642.0   
3                   0.0                    0.0                 0.0   
4                   0.0                    0.0              4256.0   

   April_Hospitalized  May_Hospitalized  June_Hospitalized  January_InICU  \
0                 0.0               0.0                0.0            0.0   
1                 0.0               0.0                0.0            0.0   
2           1635564.0         2646229.0            89703.0            0.0   
3                 0.0               0.0                0.0            0.0   
4             89847.0          206062.0             8127.0            0.0   

   February_InICU  March_InICU  April_InICU  May_InICU  June_InICU  \
0             0.0          0.0          0.0        0.0         0.0   
1             0.0          0.0          0.0        0.0         0.0   
2             0.0          0.0          0.0        0.0         0.0   
3             0.0          0.0          0.0        0.0         0.0   
4             0.0          0.0       4463.0    47440.0      1800.0   

   January_onVentilatorCumulative  February_onVentilatorCumulative  \
0                             0.0                              0.0   
1                             0.0                              0.0   
2                             0.0                              0.0   
3                             0.0                              0.0   
4                             0.0                              0.0   

   March_onVentilatorCumulative  April_onVentilatorCumulative  \
0                           0.0                           0.0   
1                           0.0                           0.0   
2                           0.0                           0.0   
3                           0.0                           0.0   
4                           0.0                           0.0   

   May_onVentilatorCumulative  June_onVentilatorCumulative  January_Positive  \
0                         0.0                          0.0               0.0   
1                         0.0                          0.0               0.0   
2                         0.0                          0.0               0.0   
3                   

In [3]:
plan_category = df.pivot_table(index = "Plan",values = "Institution", aggfunc = np.count_nonzero)
plan_category

Institution
Plan                                         
Considering a range of scenarios           69
Planning for in-person                    638
Planning for online                        81
Proposing a hybrid model                  185
Waiting to decide                          46

# Preprocessing data for Mapping

In [4]:
#Putting Universities' plan and Covid19 data on the Map
df["State_Full"]= df["State"].apply(lambda x: us.states.lookup(x).name)
df["Total_Death"] = df.March_Death +df.April_Death+df.June_Death
df["Total_Positive"]= df.March_Positive + df.April_Positive+df.June_Positive
covid = df.pivot_table(index = "State_Full",values = ["Total_Positive","Total_Death"])
covid.reset_index(inplace = True)

states_geo = gpd.read_file("gz_2010_us_040_00_500k.json")
geo = r"gz_2010_us_040_00_500k.json"
with open(geo) as communities_file:
    communities_json = json.load(communities_file)
denominations_json = []
for index in range(len(communities_json['features'])):
    denominations_json.append(communities_json['features'][index]['properties']["NAME"])
denominations_json.sort()
denominations_json

['Alabama',
 'Alaska',
 'Arizona',
 'Arkansas',
 'California',
 'Colorado',
 'Connecticut',
 'Delaware',
 'District of Columbia',
 'Florida',
 'Georgia',
 'Hawaii',
 'Idaho',
 'Illinois',
 'Indiana',
 'Iowa',
 'Kansas',
 'Kentucky',
 'Louisiana',
 'Maine',
 'Maryland',
 'Massachusetts',
 'Michigan',
 'Minnesota',
 'Mississippi',
 'Missouri',
 'Montana',
 'Nebraska',
 'Nevada',
 'New Hampshire',
 'New Jersey',
 'New Mexico',
 'New York',
 'North Carolina',
 'North Dakota',
 'Ohio',
 'Oklahoma',
 'Oregon',
 'Pennsylvania',
 'Puerto Rico',
 'Rhode Island',
 'South Carolina',
 'South Dakota',
 'Tennessee',
 'Texas',
 'Utah',
 'Vermont',
 'Virginia',
 'Washington',
 'West Virginia',
 'Wisconsin',
 'Wyoming']

# Mapping Universities and Covid19 data using Folium

In [7]:
#Mapping 
fig = Figure(width = 900, height = 500)
def color (plan):
    if plan == "Considering a range of scenarios":
        col = "gray"
    elif plan == "Planning for in-person":
        col = "green"
    elif plan == "Planning for online":
        col = "blue"
    elif plan == "Proposing a hybrid model":
        col = "orange"
    else:
        col = "lightgray"
    return col
# school_icon = folium.features.CustomIcon(icon_image = "graduation-cap", icon_size = (10,10))
m = folium.Map(location = [37.090240,-95.712891], zoom_start = 4)
minimap = plugins.MiniMap(toogle_display = True)
m.add_child(minimap)
plugins.ScrollZoomToggler().add_to(m)
plugins.Fullscreen(position="topright").add_to(m)
icon_img = os.path.abspath("school.png")
icon = folium.features.CustomIcon(icon_img,icon_size = (5,5))

fg = folium.FeatureGroup(name = "Plan")
fg_1 = folium.FeatureGroup(name = "Planning for in-person",show = False)
fg_2 = folium.FeatureGroup(name = "Planning for online",show = False)
fg_3 = folium.FeatureGroup(name = "Considering a range of scenarios",show = False)
fg_4 = folium.FeatureGroup(name = "Proposing a hybrid model",show = False)
fg_5 = folium.FeatureGroup(name = "Waiting to decide",show = False)

for index,row in df.iterrows():
    fg.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"],icon = folium.Icon(icon = "university",color = color(row["Plan"]))))
    if row["Plan"] =="Planning for in-person":
        fg_1.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"],icon= folium.Icon(icon = "university",color = color(row["Plan"]))))
    if row["Plan"] =="Planning for online":
        fg_2.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"], icon= folium.Icon(icon = "university",color = color(row["Plan"]))))
    if row["Plan"] =="Considering a range of scenarios":
        fg_3.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"],icon= folium.Icon(icon = "university",color = color(row["Plan"]))))
    if row["Plan"] =="Proposing a hybrid model":
        fg_4.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"],icon= folium.Icon(icon = "university",color = color(row["Plan"]))))
    if row["Plan"] =="Waiting to decide":
        fg_5.add_child(folium.Marker([row["Lat"],row["Long"]],tooltip=row["Institution"],popup = row["Plan"],icon= folium.Icon(icon = "university",color = color(row["Plan"]))))

m.choropleth(name = "Covid19 Positive Cases",
    geo_data = geo,data = covid,
    columns = ["State_Full","Total_Positive"],
    key_on = "feature.properties.NAME",
    fill_color = "YlGnBu", fill_opacity = 0.7,    
    legend_name = "Case Positive #",
    line_opacity = 0.2, show = False,
    smooth_factor = 1)

m.choropleth(name = "Covid19 Death #",
    geo_data = geo,data = covid,
    columns = ["State_Full","Total_Death"],
    key_on = "feature.properties.NAME",
    fill_color = "YlOrRd", fill_opacity = 0.7,
    line_opacity = 0.2,show = False,       
    legend_name = "Death Positive #", smooth_factor = 0)
m.add_child(fg)   
m.add_child(fg_1)   
m.add_child(fg_2)   
m.add_child(fg_3)   
m.add_child(fg_4)   
m.add_child(fg_5)   
m.add_child(folium.LayerControl())

m

Unfortunately Github is not able to display map.
 Please refer to the link below to see Map: 
https://nbviewer.jupyter.org/url/dmanvn.github.io/Mapping.ipynb

In [6]:
m.save("covid19_universities.html")